In [15]:
from init import *
from kiwi import make_kiwi
from datetime import datetime, timedelta, timezone
from mongo_connect import *
from tokenize_video import tokenize_video
from analyze import *
CATEGORIES = {
    "News & Politics": "25",
    'Music' : "10",
    'Sports' : "17",
    'Gaming' : "20",
    'Science & Technology': "28"
}

def main():
    
    # 1. 동영상 데이터 가져오고 저장하기기
    store_trending_videos_with_comments(db_name="raw_video_data", collection_name="raw_video_data")
    # 2. 데이터 가져오기
    data = get_data_by_date_and_category(from_date_str= "2024-03-29", db_name= "raw_video_data",collection_name="raw_video_data")
    # 3. kiwi 학습하기
    kiwi_objects = make_kiwi(data)
    # 4.tokenize하기
    proceesd_data = tokenize_video(data, kiwi_objects)
    # 5. 키워드 점수 매기기
    scored_data = score_video_keywords(proceesd_data)
    # 6. 키워드 점수 합치기, 저장장
    store_combine_video_keyword_scores(db_name= "keyword", collection_name= " keyword", data = scored_data)
    
    
    # 5. 데이터 조회
    
    kiwi_objects = make_kiwi(data)

    
    


In [19]:
from pymongo import MongoClient
from datetime import datetime, timedelta, timezone
from collections import defaultdict
from fetch_video import *

client = MongoClient("mongodb://localhost:27017")

CATEGORIES = {
    "News & Politics": "25",
    'Music' : "10",
    'Sports' : "17",
    'Gaming' : "20",
    'Science & Technology': "28"
}

def get_utc_range_from_kst_date(kst_date_str):
    """
    KST 기준 날짜 문자열을 받아, UTC 기준 시작/종료 시간 범위를 반환

    예: '2025-03-30' → 2025-03-29T15:00:00Z ~ 2025-03-30T15:00:00Z
    """
    KST = timezone(timedelta(hours=9))

    # 1️⃣ 입력 날짜 문자열을 datetime으로 (KST 기준)
    start_kst = datetime.strptime(kst_date_str, "%Y-%m-%d").replace(tzinfo=KST)
    end_kst = start_kst + timedelta(days=1)

    # 2️⃣ UTC로 변환
    start_utc = start_kst.astimezone(timezone.utc)
    end_utc = end_kst.astimezone(timezone.utc)

    return start_utc, end_utc

def get_data_by_date_and_category(kst_date_str, db_name, collection_name):
    """
    지정한 날짜부터 오늘까지의 데이터를 MongoDB에서 가져오고,
    카테고리별로 그룹화하여 반환합니다.

    Args:
        from_date_str (str): 시작 날짜 (예: '2023-10-01')
        db_name (str): MongoDB 데이터베이스 이름
        collection_name (str): 컬렉션 이름

    Returns:
        dict: {category_id: [video1, video2, ...], ...}
    """
    db = client[db_name]
    collection = db[collection_name]

    start_utc, end_utc = get_utc_range_from_kst_date(kst_date_str)

    print("쿼리 시작 시각 (UTC):", start_utc)
    print("쿼리 종료 시각 (UTC):", end_utc)

    query = {
        "timestamp": {
            "$gte": start_utc,
            "$lt": end_utc
        }
    }

    results = list(collection.find(query))
    print(f"📦 조회된 문서 수: {len(results)}")

    # 카테고리별로 그룹화
    grouped = defaultdict(list)
    for doc in results:
        cat_id = doc.get("metadata", {}).get("category_id")
        if cat_id:
            grouped[cat_id].append(doc)

    return dict(grouped)




data = get_data_by_date_and_category(kst_date_str= "2025-03-31", db_name= "raw_video_data",collection_name="raw_video_data")
data

쿼리 시작 시각 (UTC): 2025-03-30 15:00:00+00:00
쿼리 종료 시각 (UTC): 2025-03-31 15:00:00+00:00
📦 조회된 문서 수: 425


{'25': [{'_id': ObjectId('67e93754b6667caf93eee293'),
   'timestamp': datetime.datetime(2025, 3, 31, 12, 7, 0, 803000),
   'metadata': {'category_id': '25'},
   'video_id': '7IdEdSp9ads',
   'title': '[뉴스 \'꾹\'] "야! 사진 찍으러 왔나? 불 꺼!" 고성 지르자 이재명 반응이.. (2025.03.27/MBC뉴스)',
   'description': '#이재명 #산불 #항의\n#MBC #뉴스 #뉴스데스크 #MBC뉴스 #뉴스투데이 #뉴스ZIP #뉴스꾹 #오늘이뉴스 #자막뉴스\nㅤ\nⓒ MBC & iMBC 무단 전재, 재배포 및 이용(AI학습 포함)금지',
   'tags': ['MBC',
    'MBC뉴스',
    '뉴스데스크',
    'newsdesk',
    '뉴스투데이',
    'newstoday',
    '8시뉴스',
    '아침뉴스',
    '뉴스',
    '정오뉴스',
    'news',
    '실시간',
    '실시간 뉴스',
    '엠비씨 뉴스',
    '엠비씨',
    '뉴스 실시간',
    '뉴스속보',
    'genre:정치',
    'format:리포트',
    'type:디지털',
    'source:영상',
    'series:오늘 이 뉴스',
    'topic:이재명 청송대피소 방문',
    'person:이재명',
    'location:서울mbc',
    'language:한국어',
    'custom:2차가공',
    'custom:일반'],
   'duration': '0:05:16',
   'view_count': 3784949,
   'like_count': 73330,
   'comment_count': 1000,
   'comments': ['제발',
    '전직 소방관들 100 방화라고 함',
    '힘든국